In [1]:
import pandas as pd
from datetime import timezone
from datetime import datetime
import numpy as np 
import altair as alt 

In [2]:
#loads in datasets, filepath is locatoin of file, token is the 3 letter id (string) of the token

    
def pre_processing(df, token, long):
    if long:
        df['Change'] = df['Open'] - df['Adj Close']
        df['Max Close'] = df['Close'].max()
        df['Mean Close'] = df['Close'].mean()
        df['percent_change'] = (df['Adj Close'] - df['Open']) / df['Adj Close']
        df['token'] = token
    else:
        df[token + '_Change'] = df['Open'] - df['Adj Close']
        df[token + '_Max_Close'] = df['Close'].max()
        df[token + '_Mean_Close'] = df['Close'].mean()
        df[token + '_percent_change'] = (df['Adj Close'] - df['Open']) / df['Adj Close']
        df[token + '_Open'] = df['Open']
        df[token + '_Close'] = df['Close']
        df[token + '_Adj Close'] = df['Adj Close']
        df[token + '_high'] = df['High']
        df[token + '_Low'] = df['Low']
        df[token + '_Volume'] = df['Volume']
        df = df.drop(['Open', 'Close', 'Adj Close', 'High', 'Low', 'Volume', 'token'], axis=1)
    return df

#joins data in a "wide" form, adding new columnes for each additional token
def load_wide_data(df, existing_df):
    final_df = existing_df.merge(df, how="inner", on="Date")
    return final_df

#concats columns in a SQL-Union style join
def concatenator(df_list):
    union_df = pd.concat(df_list)
    return union_df




In [8]:

ada_df = pd.read_csv('ADA-USD.csv')
eth_df = pd.read_csv('ETH-USD.csv')
btc_df = pd.read_csv('BTC-USD.csv')
xrp_df = pd.read_csv('XRP-USD.csv')
trx_df = pd.read_csv('TRX-USD.csv')
doge_df = pd.read_csv('DOGE-USD.csv')
ltc_df = pd.read_csv('LTC-USD.csv')
bch_df = pd.read_csv('BCH-USD.csv')
vnq_df = pd.read_csv('VNQ.csv')
spy_df = pd.read_csv('SPY.csv')

dfs = [ada_df, eth_df, btc_df, xrp_df, trx_df, doge_df, ltc_df, bch_df, vnq_df, spy_df]
tokens = ['ADA', 'ETH','BTC', 'XRP', 'TRX', 'DOGE', 'LTC', 'BCH', 'VNQ', 'SPY']

final_union_df = pre_processing(ada_df.copy(), 'ADA', True)
all_prices_df = pd.DataFrame(ada_df['Date'])



for i, df in enumerate(dfs):
     final_union_df = concatenator([pre_processing(df, tokens[i], True), final_union_df])
     all_prices_df = load_wide_data(pre_processing(df, tokens[i], False), all_prices_df)
    
    






/opt/python/envs/default/lib/python3.8/site-packages/pandas/core/frame.py:9190: FutureWarning: Passing 'suffixes' which cause duplicate columns {'Max Close_x', 'Mean Close_x', 'percent_change_x', 'Change_x'} in the result is deprecated and will raise a MergeError in a future version.
  return merge(


In [4]:
final_union_df.head()

Date 
 Open 
 High 
 Low 
 Close 
 Adj Close 
 Volume 
 Change 
 Max Close 
 Mean Close 
 percent_change 
 token 
 
 
 
 
 0 
 2020-12-31 
 84.089996 
 85.050003 
 83.400002 
 84.930000 
 83.323059 
 4827300.0 
 0.766937 
 110.919998 
 99.092375 
 -0.009204 
 VNQ 
 
 
 1 
 2021-01-04 
 85.199997 
 85.279999 
 82.070000 
 82.169998 
 80.615288 
 5311500.0 
 4.584709 
 110.919998 
 99.092375 
 -0.056871 
 VNQ 
 
 
 2 
 2021-01-05 
 82.169998 
 82.870003 
 82.129997 
 82.290001 
 80.733017 
 4932600.0 
 1.436981 
 110.919998 
 99.092375 
 -0.017799 
 VNQ 
 
 
 3 
 2021-01-06 
 82.260002 
 82.970001 
 81.730003 
 82.430000 
 80.870369 
 6520100.0 
 1.389633 
 110.919998 
 99.092375 
 -0.017183 
 VNQ 
 
 
 4 
 2021-01-07 
 82.500000 
 82.540001 
 81.750000 
 82.269997 
 80.713394 
 4068400.0 
 1.786606 
 110.919998 
 99.092375 
 -0.022135 
 VNQ

In [4]:
corr_matrix = all_prices_df.corr().reset_index().melt('index')
corr_matrix

index 
 variable 
 value 
 
 
 
 
 0 
 Change_x 
 Change_x 
 1.000000 
 
 
 1 
 Max Close_x 
 Change_x 
 NaN 
 
 
 2 
 Mean Close_x 
 Change_x 
 NaN 
 
 
 3 
 percent_change_x 
 Change_x 
 -0.896937 
 
 
 4 
 ADA_Change 
 Change_x 
 1.000000 
 
 
 ... 
 ... 
 ... 
 ... 
 
 
 15871 
 VNQ_Close 
 VNQ_Volume 
 -0.247410 
 
 
 15872 
 VNQ_Adj Close 
 VNQ_Volume 
 -0.238303 
 
 
 15873 
 VNQ_high 
 VNQ_Volume 
 -0.230067 
 
 
 15874 
 VNQ_Low 
 VNQ_Volume 
 -0.253242 
 
 
 15875 
 VNQ_Volume 
 VNQ_Volume 
 1.000000 
 
 
 
 15876 rows × 3 columns

# **Questions to Ask**
- What time period is appropriate for crypto volatility?
- What other risk/financial comparisons are useful?

**Notes**

- Need to create one selector for all visualizations, figure out how to include multiple selectors in visualizations
consider using facet to break out performance if layered/stacked charts become too common. 
- Having issue with scatterplot, once it's finished it should work better.
- implement mean line for some value metric [link](https://altair-viz.github.io/gallery/selection_layer_bar_month.html)
- implement comparison to other assets (Real estate, S&P etc)
    - include volatility, price, and other metrics
- need to make correlation matrix [link](https://github.com/altair-viz/altair/pull/1945)
- inspiration [link](https://www.youtube.com/watch?v=XWdcpoXKRnk)
- 

In [8]:
base = alt.Chart(corr_matrix).transform_filter(
    alt.datum.index < alt.datum.variable
).encode(
    x='index',
    y='variable',
).properties(
    width=alt.Step(50),
    height=alt.Step(50)
)

rects = base.mark_rect().encode(
    color='value'
)

text = base.mark_text(
    size=18
).encode(
    text=alt.Text('value', format=".2f"),
    color=alt.condition(
        "datum.value > 0.5",
        alt.value('white'),
        alt.value('black')
    )
)

rects + text

alt.LayerChart(...)

In [9]:

label_list = ['All'] + list(final_union_df['token'].unique())

input_dropdown1 = alt.binding_select(options=[None] + list(final_union_df['token'].unique()), labels=label_list)
token_selector = alt.selection_single(name='Currency: ', fields=['token'], bind=input_dropdown1)
#brush = alt.selection(type='interval')

open_close_color = alt.condition("datum.Open <= datum.Close",
                                 alt.value("#06982d"),
                                 alt.value("#ae1325"))

#scales = alt.selection_interval(bind='scales')


base = alt.Chart(final_union_df).encode(
    alt.X('Date:T', 
          axis=alt.Axis(
              format='%m/%d',
              labelAngle=-45,
              title='Date'
          )
    ),
    color=open_close_color, 
    tooltip=[alt.Tooltip('Date:T', format='%m/%d'), alt.Tooltip('Open:Q', format='$'), 
             alt.Tooltip('Close:Q', format='$'), alt.Tooltip('Volume:Q', format='$'),
             alt.Tooltip('token:O')]
)
#

rule = base.mark_rule().encode(
    alt.Y(
        'Low:Q',
        title='Price',
        scale=alt.Scale(zero=False),
    ),
    alt.Y2('High:Q')
)

bar = base.mark_bar().encode(
    alt.Y('Open:Q'),
    alt.Y2('Close:Q')
)

all = rule + bar
all.add_selection(token_selector).transform_filter(token_selector).interactive()

In [10]:
#test which one they like better: drop down or bar plot with token names
#consider adding trend line(s)

label_list = ['All'] + list(final_union_df['token'].unique())

input_dropdown1 = alt.binding_select(options=[None] + list(final_union_df['token'].unique()), labels=label_list)
token_selector1 = alt.selection_single(name='Currency: ', fields=['token'], bind=input_dropdown1)
#token_selector2 = alt.selection_single(name='x_axis', fields=['token'], bind=input_dropdown)
brush = alt.selection(type='interval')
multi = alt.selection(type='multi')

#scales = alt.selection_interval(bind='scales')

#select time period with this small chart
small = alt.Chart(final_union_df).mark_bar(tooltip=True).encode(
    x=alt.X('Date:T', title='Date', axis=alt.Axis(format='%m/%d', labelAngle=-45), )
    #,y=alt.Y('Date:T', axis=alt.Axis(format='%m/%y', labelAngle=-45))
    ,color=alt.condition(brush, alt.value('red'), alt.value('grey'))
    ).add_selection(brush).properties(width=875, height=100)

#select multiple tokens with this small chart
tokens = alt.Chart(final_union_df).mark_bar(tooltip=True).encode(
    x=alt.X('token:O', title=None, axis=alt.Axis(labelAngle=-45))
    ,color=alt.condition(brush, alt.value('blue'), alt.value('grey'))
    ).add_selection(brush).properties(width=875, height=100)


#bar height is max price for each token?

large = alt.Chart(final_union_df).mark_circle(tooltip=True).encode(
    x=alt.X('Date:T', title='Date', axis=alt.Axis(format='%m/%d/%y', labelAngle=-45))
    ,y=alt.Y('percent_change:Q', title='Percent Change', axis=alt.Axis(format='%',  labels=True, tickSize=0))
    ,color='token'
    #alt.condition(brush, alt.value('red'), alt.value('grey'))
    ).add_selection(
         token_selector1
         ).transform_filter(
             token_selector1).transform_filter(brush).properties(
                     width=875, height=600).interactive()
    


both = alt.vconcat(small, tokens)
both = alt.vconcat(both, large)
both.configure_legend(
        strokeColor='gray',
    fillColor='#EEEEEE',
    padding=10,
    cornerRadius=10,
    orient='top-right'
)
both

In [19]:
#test which one they like better: drop down or bar plot with token names
#consider adding trend line(s)

label_list = ['All'] + list(final_union_df['token'].unique())

input_dropdown1 = alt.binding_select(options=[None] + list(final_union_df['token'].unique()), labels=label_list)
token_selector1 = alt.selection_single(name='Currency: ', fields=['token'], bind=input_dropdown1)
#token_selector2 = alt.selection_single(name='x_axis', fields=['token'], bind=input_dropdown)
brush = alt.selection(type='interval')
brush2 = alt.selection(type='interval')


#scales = alt.selection_interval(bind='scales')

#select time period with this small chart
small = alt.Chart(final_union_df).mark_bar(tooltip=True).encode(
    x=alt.X('Date:T', title='Date', axis=alt.Axis(format='%m/%d', labelAngle=-45), )
    #,y=alt.Y('Date:T', axis=alt.Axis(format='%m/%y', labelAngle=-45))
    ,color=alt.condition(brush, alt.value('red'), alt.value('grey'))
    ).add_selection(brush).properties(width=875, height=100)

#select multiple tokens with this small chart
tokens = alt.Chart(final_union_df).mark_bar(tooltip=True).encode(
    x=alt.X('token:O', title=None, axis=alt.Axis(labelAngle=-45))
    ,color=alt.condition(brush, alt.value('blue'), alt.value('grey'))
    ).add_selection(brush2).properties(width=875, height=100)


#bar height is max price for each token?

large = alt.Chart(final_union_df).mark_line(tooltip=True).encode(
    x=alt.X('Date:T', title='Date', axis=alt.Axis(format='%m/%d/%y', labelAngle=-45))
    ,y=alt.Y('percent_change:Q', title='Percent Change', axis=alt.Axis(format='%',  labels=True, tickSize=0))
    ,color='token'
    #alt.condition(brush, alt.value('red'), alt.value('grey'))
    ).add_selection(
         token_selector1
         ).transform_filter(
             token_selector1).transform_filter(brush).transform_filter(brush2).properties(
                     width=875, height=600).interactive()
    


both = alt.vconcat(small, tokens)
both = alt.vconcat(both, large)
both.configure_legend(
        strokeColor='gray',
    fillColor='#EEEEEE',
    padding=10,
    cornerRadius=10,
    orient='top-right'
)
both

In [0]:
#crypto price vs other commodities/real assets (in USD)

# **Noor's Visualizations**

In [7]:
# Temporary  - will merge w/ Marcus pre-processing stuff later:
ada_df = pd.read_csv('ADA-USD.csv')
eth_df = pd.read_csv('ETH-USD.csv')
btc_df = pd.read_csv('BTC-USD.csv')
xrp_df = pd.read_csv('XRP-USD.csv')
trx_df = pd.read_csv('TRX-USD.csv')
doge_df = pd.read_csv('DOGE-USD.csv')
ltc_df = pd.read_csv('LTC-USD.csv')
bch_df = pd.read_csv('BCH-USD.csv')


ada_df['token'] = 'ADA'
eth_df['token'] = 'ETH'
btc_df['token'] = 'BTC'
xrp_df['token'] = 'XRP'
trx_df['token'] = 'TRX'
doge_df['token'] = 'DOGE'
ltc_df['token'] = 'LTC'
bch_df['token'] = 'BCH'

def pre_processing(df):
    df['Change'] = df['Open'] - df['Adj Close']
    df['Max Close'] = df['Close'].max()
    df['Mean Close'] = df['Close'].mean()
    return df
    
df_list = [ada_df, eth_df, btc_df, xrp_df, trx_df, doge_df, ltc_df, bch_df]
for df in df_list:
    pre_processing(df)

def concatenator(df_list):
    union_df = pd.concat(df_list)
    union_df['percent_change'] = (union_df['Adj Close'] - union_df['Open']) / union_df['Adj Close'] 
    return union_df

union_df = concatenator(df_list)
union_df.head()

Date 
 Open 
 High 
 Low 
 Close 
 Adj Close 
 Volume 
 token 
 Change 
 Max Close 
 Mean Close 
 percent_change 
 
 
 
 
 0 
 2020-12-31 
 0.184034 
 0.185749 
 0.176594 
 0.181397 
 0.181397 
 1.132268e+09 
 ADA 
 0.002637 
 2.968239 
 1.46308 
 -0.014537 
 
 
 1 
 2021-01-01 
 0.181382 
 0.184246 
 0.172022 
 0.175350 
 0.175350 
 1.122218e+09 
 ADA 
 0.006032 
 2.968239 
 1.46308 
 -0.034400 
 
 
 2 
 2021-01-02 
 0.175359 
 0.184253 
 0.169233 
 0.177423 
 0.177423 
 1.408850e+09 
 ADA 
 -0.002064 
 2.968239 
 1.46308 
 0.011633 
 
 
 3 
 2021-01-03 
 0.177382 
 0.208679 
 0.173376 
 0.204995 
 0.204995 
 2.303858e+09 
 ADA 
 -0.027613 
 2.968239 
 1.46308 
 0.134701 
 
 
 4 
 2021-01-04 
 0.205236 
 0.239661 
 0.194450 
 0.224762 
 0.224762 
 3.260699e+09 
 ADA 
 -0.019526 
 2.968239 
 1.46308 
 0.086874

In [18]:
selection = alt.selection_multi(fields=['token'], bind='legend')

chart = alt.Chart(final_union_df).mark_bar().encode(
    alt.X("Date:T"),
    alt.Y("percent_change:Q", title='Percentage Change'),
    color=alt.condition("datum.percent_change < 0",
                                 alt.value("#ae1325"),
                                 alt.value("#06982d")),
    tooltip= ['Date:T', 'percent_change']
).add_selection(
    selection
).properties(height=500, width=800, title='Percentage Change of Currency Over Time')

input_dropdown1 = alt.binding_select(options=[None] + list(final_union_df['token'].unique()), labels=label_list)
token_selector = alt.selection_single(name='Currency: ', fields=['token'], bind=input_dropdown1)
chart.add_selection(token_selector).transform_filter(token_selector).interactive()

In [19]:
selection = alt.selection_multi(fields=['token'], name='Currency')

chart = alt.Chart(final_union_df).mark_circle().encode(
    x=alt.X('yearmonth(Date)', title='Date'),
    y=alt.Y('mean(Close)', axis=alt.Axis(title='Average Closing Price (in USD)')),
    size = alt.Size('mean(Volume):Q',
        legend=alt.Legend(title='Average Volume Traded')
    ),
    tooltip=['yearmonth(Date)', 'mean(Close)', 'mean(Volume)']
).properties(title='Price of Currency Over Course of Year With Size Encoded by Volume Traded', width=800, height=500).add_selection(
    selection
)

lineplot = alt.Chart(final_union_df).mark_line().encode(
    x=alt.X('yearmonth(Date)', title='Date'),
    y=alt.Y('mean(Close)'),
    tooltip=['yearmonth(Date)', 'mean(Close)', 'mean(Volume)']
)

both = chart + lineplot

input_dropdown1 = alt.binding_select(options=[None] + list(final_union_df['token'].unique()), labels=label_list)
token_selector = alt.selection_single(name='Currency: ', fields=['token'], bind=input_dropdown1)
both.add_selection(token_selector).transform_filter(token_selector).interactive()

In [20]:
selection = alt.selection_multi(fields=['token'], bind='legend')

chart = alt.Chart(final_union_df).mark_line().encode(
    alt.X("Date:T"),
    alt.Y("Close:Q", title='Close'),
    tooltip= ['Date:T', 'Close:Q']
).add_selection(
    selection
).transform_filter(selection).properties(height=500, width=800, title='Closing Price Over Time')

moving_avg = alt.Chart(final_union_df).mark_line(
    color='red',
    size=3
).transform_window(
    rolling_mean='mean(Close)'
).encode(
    x='Date:T',
    y='rolling_mean:Q'
)

both = chart + moving_avg

input_dropdown1 = alt.binding_select(options=[None] + list(final_union_df['token'].unique()), labels=label_list)
token_selector = alt.selection_single(name='Currency: ', fields=['token'], bind=input_dropdown1)
both.add_selection(token_selector).transform_filter(token_selector).interactive()

In [21]:
btc_reddit_data = pd.read_csv('reddit_posts_btc.csv')
btc_reddit_data['mentioned?'] = btc_reddit_data.selftext.str.contains('BTC', case=True, flags=0) | btc_reddit_data.title.str.contains('BTC', case=True, flags=0)| btc_reddit_data.title.str.contains('Bitcoin', case=True, flags=0)| btc_reddit_data.selftext.str.contains('Bitcoin', case=True, flags=0)| btc_reddit_data.title.str.contains('bitcoin', case=True, flags=0)| btc_reddit_data.selftext.str.contains('bitcoin', case=True, flags=0)
btc_reddit_data['mentioned?'] = btc_reddit_data['mentioned?'].astype(int)
# btc_reddit_data['created_utc'] = datetime.utcfromtimestamp(btc_reddit_data['created_utc'])
btc_reddit_data.head()

id 
 created_utc 
 selftext 
 title 
 mentioned? 
 
 
 
 
 0 
 nd6v9r 
 5/15/2021 21:43 
 NaN 
 A little old news, but I found it valid (March... 
 1 
 
 
 1 
 nd6vgo 
 5/15/2021 21:44 
 Bitcoin's meteoric rise to an ATH of $63,000 h... 
 Have you lost money on Bitcoin? This is your c... 
 1 
 
 
 2 
 nd6zb7 
 5/15/2021 21:49 
 PLEASE READ! I've tried posting on other subs ... 
 Binoix Scam Beware 
 0 
 
 
 3 
 nd74vw 
 5/15/2021 21:57 
 Did Mr musk make some whales and retail buyers... 
 Is bitcoin going bear or is it alt coin season 
 1 
 
 
 4 
 nd79ys 
 5/15/2021 22:04 
 I totally understand that there is an environm... 
 Wallstreet is a bunch of babies sometimes. Sto... 
 0

In [24]:
#need to debug to display viz

selection = alt.selection_multi(fields=['token'], bind='legend')

chart = alt.Chart(final_union_df).mark_line().encode(
    alt.X("Date:T"),
    alt.Y("Close:Q", title='Close',
    tooltip= ['Date:T', 'Close:Q']
)).add_selection(
    selection
).transform_filter(selection).properties(height=500, width=800, title='Closing Price Over Time')

moving_avg = alt.Chart(final_union_df).mark_line(
    color='red',
    size=3
).transform_window(
    rolling_mean='mean(Close)'
).encode(
    x='Date:T',
    y='rolling_mean:Q'
)

both = chart + moving_avg

input_dropdown1 = alt.binding_select(options=[None] + list(final_union_df['token'].unique()), labels=label_list)
token_selector = alt.selection_single(name='Currency: ', fields=['token'], bind=input_dropdown1)

both.add_selection(token_selector).transform_filter(token_selector).interactive()

alt.LayerChart(...)